In [2]:
# IMPORT STATEMENTS
import math
import numpy as np
import pandas as pd

import os
import sys
sys.path.insert(0, "/Users/rohan/public_html/Hegemon/Data2/Data")
from moreprocessing import *
sys.path.append("/Users/rohan/public_html/Hegemon")
import StepMiner as smn
import HegemonUtil as hu

In [40]:
# Fix expr file 
# process.py generated GSE202108-counts.txt from txt.gz files for each GSMID in ./raw
expr = pd.DataFrame(pd.read_csv("GSE202108-counts.txt", sep = "\t", header=0))
expr = expr.drop(0, axis=0)
expr.insert(0, 'Name', expr["Gene"])
expr.insert(0, 'ProbeID', expr["Gene"])
expr = expr.drop("Gene", axis=1)
expr

ProbeID     Name GSM6094651 GSM6094647 GSM6094648 GSM6094650  \
1         Xkr4     Xkr4     -5.052     -5.052     -5.052     -5.052   
2          Rp1      Rp1     -5.052     -5.052     -5.052     -5.052   
3        Sox17    Sox17     -3.245     -3.992     -4.287      -2.85   
4       Mrpl15   Mrpl15      6.318       4.79      4.905      6.298   
5       Lypla1   Lypla1      6.058      6.548      7.027      5.979   
...        ...      ...        ...        ...        ...        ...   
23416  Gm20816  Gm20816     -5.052     -5.052     -5.052     -5.052   
23417  Gm20867  Gm20867     -5.052     -5.052     -5.052     -5.052   
23418  Gm20806  Gm20806     -5.052     -5.052     -5.052     -5.052   
23419  Gm20854  Gm20854     -5.052     -5.052     -5.052     -5.052   
23420    Erdr1    Erdr1      4.575      3.048      3.421       4.09   

      GSM6094649 GSM6094646  
1         -5.052     -5.052  
2         -5.052     -5.052  
3         -4.922     -4.922  
4          6.602      5.056  
5           6.29      6.919  
...          ...        ...  
23416     -5.052     -5.052  
23417     -5.052     -5.052  
23418     -5.052     -5.052  
23419     -5.052     -5.052  
23420      4.367      3.001  

[23420 rows x 8 columns]

In [41]:
genes = expr.loc[:,["ProbeID", "Name"]]
cols = expr.columns
expr = expr.drop(['ProbeID', 'Name'], axis=1)

# This is to get rid of negative expression values (results from log2 normalization before CPM)
typedict = {i:np.float64 for i in list(expr.columns)}
expr = expr.astype(typedict)
expr = expr.apply(lambda x: 2**x, axis = 0)

# Normalize and log transform
expr = sc.AnnData(expr.T)
sc.pp.normalize_total(expr, target_sum=1e6)
sc.pp.log1p(expr, base = 2)

expr = pd.DataFrame(expr.X)
expr = expr.T
expr.insert(0, "Name", genes["Name"])
expr.insert(0, "ProbeID", genes["ProbeID"])
expr.columns = cols

expr

/usr/local/lib/python3.6/dist-packages/anndata/_core/anndata.py:119: ImplicitModificationWarning: Transforming to str index.
  warnings.warn("Transforming to str index.", ImplicitModificationWarning)


ProbeID     Name  GSM6094651  GSM6094647  GSM6094648  GSM6094650  \
0          NaN      NaN    0.043016    0.043229    0.042879    0.043066   
1         Xkr4     Xkr4    0.043016    0.043229    0.042879    0.043066   
2          Rp1      Rp1    0.145226    0.088708    0.072128    0.188300   
3        Sox17    Sox17    6.341727    4.853806    4.953479    6.323641   
4       Mrpl15   Mrpl15    6.085235    6.576230    7.039160    6.009092   
...        ...      ...         ...         ...         ...         ...   
23415  Gm21943  Gm21943    0.043016    0.043229    0.042879    0.043066   
23416  Gm20816  Gm20816    0.043016    0.043229    0.042879    0.043066   
23417  Gm20867  Gm20867    0.043016    0.043229    0.042879    0.043066   
23418  Gm20806  Gm20806    0.043016    0.043229    0.042879    0.043066   
23419  Gm20854  Gm20854    4.639888    3.224300    3.550824    4.179421   

       GSM6094649  GSM6094646  
0        0.043212    0.043024  
1        0.043212    0.043024  
2        0.047220    0.047016  
3        6.629107    5.104641  
4        6.320621    6.936913  
...           ...         ...  
23415    0.043212    0.043024  
23416    0.043212    0.043024  
23417    0.043212    0.043024  
23418    0.043212    0.043024  
23419    4.447158    3.176229  

[23420 rows x 8 columns]

In [42]:
writeExprIdx(expr)

14-Aug-2022 00:11:04 DEBUG utils - Directory /mnt/booleanfs2/sahoo/Data/BooleanLab/Rohan/Data/Data/GSE202108 already exists. Skipping.
14-Aug-2022 00:11:04 INFO GEOparse - File already exist: using local version.
14-Aug-2022 00:11:04 INFO GEOparse - Parsing /mnt/booleanfs2/sahoo/Data/BooleanLab/Rohan/Data/Data/GSE202108/GSE202108_family.soft.gz: 
14-Aug-2022 00:11:04 DEBUG GEOparse - DATABASE: GeoMiame
14-Aug-2022 00:11:04 DEBUG GEOparse - SERIES: GSE202108
14-Aug-2022 00:11:04 DEBUG GEOparse - PLATFORM: GPL24247
14-Aug-2022 00:11:04 DEBUG GEOparse - SAMPLE: GSM6094646
14-Aug-2022 00:11:04 DEBUG GEOparse - SAMPLE: GSM6094647
14-Aug-2022 00:11:04 DEBUG GEOparse - SAMPLE: GSM6094648
14-Aug-2022 00:11:04 DEBUG GEOparse - SAMPLE: GSM6094649
14-Aug-2022 00:11:04 DEBUG GEOparse - SAMPLE: GSM6094650
14-Aug-2022 00:11:04 DEBUG GEOparse - SAMPLE: GSM6094651


Writing to current directory
Starting expr at /mnt/booleanfs2/sahoo/Data/BooleanLab/Rohan/Data/Data/GSE202108/GSE202108-GPL24247-expr.txt
Done writing expr
Writing idx to /mnt/booleanfs2/sahoo/Data/BooleanLab/Rohan/Data/Data/GSE202108/GSE202108-GPL24247-idx.txt
Starting make_idx
Done with make_idx


In [43]:
%run runmoreprocessing.py

Database ID KH3
Dataset Name Shlomchik 2022 B cells
key blood:macv:
Configuration file (default /Users/rohan) 


14-Aug-2022 00:12:35 DEBUG utils - Directory /mnt/booleanfs2/sahoo/Data/BooleanLab/Rohan/Data/Data/GSE202108 already exists. Skipping.
14-Aug-2022 00:12:35 INFO GEOparse - File already exist: using local version.
14-Aug-2022 00:12:35 INFO GEOparse - Parsing /mnt/booleanfs2/sahoo/Data/BooleanLab/Rohan/Data/Data/GSE202108/GSE202108_family.soft.gz: 
14-Aug-2022 00:12:35 DEBUG GEOparse - DATABASE: GeoMiame
14-Aug-2022 00:12:35 DEBUG GEOparse - SERIES: GSE202108
14-Aug-2022 00:12:35 DEBUG GEOparse - PLATFORM: GPL24247
14-Aug-2022 00:12:35 DEBUG GEOparse - SAMPLE: GSM6094646
14-Aug-2022 00:12:35 DEBUG GEOparse - SAMPLE: GSM6094647
14-Aug-2022 00:12:35 DEBUG GEOparse - SAMPLE: GSM6094648
14-Aug-2022 00:12:35 DEBUG GEOparse - SAMPLE: GSM6094649
14-Aug-2022 00:12:35 DEBUG GEOparse - SAMPLE: GSM6094650
14-Aug-2022 00:12:35 DEBUG GEOparse - SAMPLE: GSM6094651


[KH3]
name = Shlomchik 2022 B cells
expr = /mnt/booleanfs2/sahoo/Data/BooleanLab/Rohan/Data/Data/GSE202108/GSE202108-GPL24247-expr.txt
index = /mnt/booleanfs2/sahoo/Data/BooleanLab/Rohan/Data/Data/GSE202108/GSE202108-GPL24247-idx.txt
survival = /mnt/booleanfs2/sahoo/Data/BooleanLab/Rohan/Data/Data/GSE202108/GSE202108-GPL24247-survival.txt
indexHeader = /mnt/booleanfs2/sahoo/Data/BooleanLab/Rohan/Data/Data/GSE202108/GSE202108-GPL24247-ih.txt
info = /mnt/booleanfs2/sahoo/Data/BooleanLab/Rohan/Data/Data/GSE202108/GSE202108-GPL24247-info.txt
key = blood:macv:
source = GSE202108
Write to file? y/n y


14-Aug-2022 00:12:38 DEBUG utils - Directory /mnt/booleanfs2/sahoo/Data/BooleanLab/Rohan/Data/Data/GSE202108 already exists. Skipping.
14-Aug-2022 00:12:38 INFO GEOparse - File already exist: using local version.
14-Aug-2022 00:12:38 INFO GEOparse - Parsing /mnt/booleanfs2/sahoo/Data/BooleanLab/Rohan/Data/Data/GSE202108/GSE202108_family.soft.gz: 
14-Aug-2022 00:12:38 DEBUG GEOparse - DATABASE: GeoMiame
14-Aug-2022 00:12:38 DEBUG GEOparse - SERIES: GSE202108
14-Aug-2022 00:12:38 DEBUG GEOparse - PLATFORM: GPL24247
14-Aug-2022 00:12:38 DEBUG GEOparse - SAMPLE: GSM6094646
14-Aug-2022 00:12:38 DEBUG GEOparse - SAMPLE: GSM6094647
14-Aug-2022 00:12:38 DEBUG GEOparse - SAMPLE: GSM6094648
14-Aug-2022 00:12:38 DEBUG GEOparse - SAMPLE: GSM6094649
14-Aug-2022 00:12:38 DEBUG GEOparse - SAMPLE: GSM6094650
14-Aug-2022 00:12:38 DEBUG GEOparse - SAMPLE: GSM6094651
